---

# TP 4 : Méthodes de quadrature de Gauss

<b>Polytech Sorbonne, Main 3</b><br>
Analyse numérique et EDO<br>
Auteur : Fabien Vergnet

---

## Table des matières

- [Exercice 1 : Méthodes de Gauss-Legendre](#gauss-legendre)
- [Exercice 2 : Le cas d'un domaine non borné](#gauss-hermite)
- [Exercice 3 : Intégrale de fonction singulière](#gauss-tchebychev)
- [Exercice 4 : Résolution d'EDO](#EDO)
- [Exercice 5 : Formules de quadrature en 2D](#2d)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

<a id=gauss-legendre></a>
## Exercice 1 : Méthodes de Gauss-Legendre

Dans cet exercice, nous cherchons à approcher le calcul d'une intégrale $$\displaystyle \int_a^b f(x)dx$$ avec des méthodes de quadratures de Gauss-Legendre composées. Nous nous intéresserons en particulier à l'approximation des intégrales du TP précédent

$$
\displaystyle \int_{1/2}^2 \left( 1 + \dfrac{1}{x^2} \right) \arctan(x) dx = \dfrac{3\pi}{4} \quad \text{et} \quad
\int_0^{\pi/2} \dfrac{1}{1+\sin(x)} dx = 1,
$$
dont on connait les valeurs exactes.

### Question 1

Définir la fonction `GaussLegendre2` qui prend en arguments une fonction $f$, les bornes $a$ et $b$ de l'intervalle d'intégration et un entier $N$ et qui retourne une valeur approchée de l'integrale $$\int_a^b f(x)dx$$ en utilisant la méthode de Gauss-Legendre à 2 points. On définira une subdivision de l'intervalle $[a,b]$ en $N$ intervalles afin d'implémenter une méthode de quadrature composée.

In [ ]:
def f1(x):
    return (1+1./x**2)*np.arctan(x)

def f2(x):
    return 1./(1+np.sin(x))

def GaussLegendre2(f,a,b,N):
    ### BEGIN SOLUTION
    ai = np.linspace(a,b,N+1)
    h = ai[1]-ai[0]
    xi1 = .5*(ai[:-1]+ai[1:]) - .5*h/(np.sqrt(3))
    xi2 = .5*(ai[:-1]+ai[1:]) + .5*h/(np.sqrt(3))
    return np.sum(.5*h*(f(xi1) + f(xi2)))
    ### END SOLUTION
    
### TEST
### BEGIN SOLUTION
def GaussLegendre2bis(f,a,b,N):
    ai = np.linspace(a,b,N+1)
    h = ai[1]-ai[0]
    I = 0
    for i in range(N):
        I += .5*h* f(.5*(ai[i+1]+ai[i])-.5*h/np.sqrt(3)) + .5*h*f(.5*(ai[i+1]+ai[i])+.5*h/np.sqrt(3))
    return I

I1 = GaussLegendre2(f1,0.5,2.,1)
print("I1 : solution approchée = ", I1, ", solution exacte = ", 3*np.pi/4.)
I1 = GaussLegendre2bis(f1,0.5,2.,1)
print("I1 : solution approchée = ", I1, ", solution exacte = ", 3*np.pi/4.)
I2 = GaussLegendre2(f2,0,np.pi/2.,1)
print("I2 : solution approchée = ", I2, ", solution exacte = ", 1.)
### END SOLUTION

### Question 2

Pour chaque fonction `f1` et `f2`, tracer en échelle logarithmique l'erreur de quadrature obtenue en approchant l'intégrale par la formule de Gauss-Legendre à 2 points implémentée ci-dessus en fonction du nombre de sous-intervalles $N$. Justifier le comportement observé.

In [ ]:
### BEGIN SOLUTION
def simpson(f,a,b,N):
    ai = np.linspace(a,b,N+1)
    h = ai[1:] - ai[:-1]
    fai = h/6*(f(ai[1:]) + 4*f((ai[1:] + ai[:-1])/2) + f(ai[:-1]))
    return fai.sum() 

N = np.arange(10,100,1)
E1 = np.zeros(N.size)
E2 = np.zeros(N.size)
ES1 = np.zeros(N.size)
ES2 = np.zeros(N.size)
for i in range(N.size):
    I1 = GaussLegendre2(f1,.5,2,N[i])
    I2 = GaussLegendre2(f2,0,np.pi/2.,N[i])
    E1[i] = np.abs(I1-3.*np.pi/4.)
    E2[i] = np.abs(I2-1.)
    ES1[i] = np.abs(simpson(f1,0.5,2,N[i])-3*np.pi/4)
    ES2[i] = np.abs(simpson(f2,0,np.pi/2,N[i])-1)

plt.figure(figsize=[10,8])
plt.title("Erreur de quadrature de la méthode de Gauss-Legendre à 2 points")
plt.xlabel(r"$N$")
plt.ylabel(r"$E(f)$")
plt.loglog(N,E1, label=r"$|I_G(f_1) - \dfrac{3\pi}{4}|$")
plt.loglog(N,E2,label=r"$|I_G(f_2) - 1|$")
plt.loglog(N,ES1, label=r"$|I_S(f_1) - \dfrac{3\pi}{4}|$")
plt.loglog(N,ES2,label=r"$|I_S(f_2) - 1|$")
plt.loglog(N,1./N**4,"--", label=r"$N \mapsto 1/N^4$")
plt.legend()
plt.plot()
plt.show()

# Remarque :
# On observe que l'erreur se comporte en O(h^4), ce qui est le résultat attendu puisque 
# la méthode de Gauss-Legendre à 2 points est d'ordre 3.
# Comparée à l'erreur de quadrature de la méthode de Simpson, l'erreur est un peu plus petite.
## END SOLUTION

### Question 3

Sur le graphique précédent, ajouter l'erreur de quadrature de la méthode de Simpson pour chacune des fonctions étudiées, afin de comparer les deux méthodes. Qu'observez-vous ?

### Question 4

Définir la fonction `GaussLegendre3` qui prend en arguments une fonction $f$, les bornes $a$ et $b$ de l'intervalle d'intégration et un entier $N$ et qui retourne une valeur approchée de l'integrale $$\int_a^b f(x)dx$$ en utilisant les méthodes de Gauss-Legendre à 3 points. On définira une subdivision de l'intervalle $[a,b]$ en $N$ intervalles afin d'implémenter une méthode de quadrature composée.

In [ ]:
def GaussLegendre3(f,a,b,N):
    ### BEGIN SOLUTION
    ai = np.linspace(a,b,N+1)
    h = ai[1]-ai[0]
    xi1 = .5*(ai[:-1]+ai[1:])
    xi2 = .5*(ai[:-1]+ai[1:]) - .5*np.sqrt(3)*h/np.sqrt(5)
    xi3 = .5*(ai[:-1]+ai[1:]) + .5*np.sqrt(3)*h/np.sqrt(5)
    return np.sum(.5*h*(8./9*f(xi1) + 5./9.*f(xi2) + 5./9.*f(xi3)))
    ### END SOLUTION
    
### TEST
### BEGIN SOLUTION
I1 = GaussLegendre3(f1,0.5,2.,10)
print("I1 : solution approchée = ", I1, ", solution exacte = ", 3*np.pi/4.)
I2 = GaussLegendre3(f2,0,np.pi/2.,10)
print("I2 : solution approchée = ", I2, ", solution exacte = ", 1.)
### END SOLUTION

### Question 5

Pour chaque fonction `f1` et `f2`, tracer en échelle logarithmique l'erreur de quadrature obtenue en approchant l'intégrale par la formule de Gauss-Legendre à 3 points implémentée ci-dessus, en fonction du nombre de sous-intervalles $N$. Justifier le comportement observé.


In [ ]:
### BEGIN SOLUTION
N = np.arange(10,2000,20)
E1 = np.zeros(N.size)
E2 = np.zeros(N.size)
for i in range(N.size):
    I1 = GaussLegendre3(f1,.5,2,N[i])
    I2 = GaussLegendre3(f2,0,np.pi/2.,N[i])
    E1[i] = np.abs(I1-3.*np.pi/4.)
    E2[i] = np.abs(I2-1.)

plt.figure(figsize=[10,8])
plt.title("Erreur de quadrature de la méthode de Gauss-Legendre à 3 points")
plt.xlabel(r"$N$")
plt.ylabel(r"$E(f)$")
plt.loglog(N,E1, label=r"$|I_G(f_1) - \dfrac{3\pi}{4}|$")
plt.loglog(N,E2,label=r"$|I_G(f_2) - 1|$")
plt.loglog(N,1./N**6,"--", label=r"$N \mapsto 1/N^6$")
plt.legend()
plt.plot()
plt.show()

# Remarque :
# On observe que l'erreur de quadrature se comporte en O(h^6), ce qui est le résultat attendu puisque
# la méthode de Gauss-Legendre à 3 points est d'ordre 5.
## END SOLUTION

<a id="gauss-hermite"></a>
## Exercice 2 : Le cas d'un domaine non borné

Le but de cet exercice est de mettre en place une méthode de Gauss pour l'intégrale

$$
    \int_{-\infty}^{+\infty} \cos(x) e^{-x^2}dx.
$$

Nous introduisons alors la fonction poids $\omega(x) = e^{-x^2}$, ainsi que le produit scalaire

\begin{equation*}
    \langle f,g \rangle_{\omega} = \int_{-\infty}^{+\infty} f(x)g(x) e^{-x^2} dx.
\end{equation*}

### Question 1

Définir la fonction `g` qui code pour la fonction $g(x)= \cos(x) \exp(-x^2)$ et tracer le graphe de $g$ sur l'intervalle $[-5,5]$.


In [ ]:
def g(x):
    ### BEGIN SOLUTION
    return np.cos(x)*np.exp(-x**2)
    ### END SOLUTION
    
# Graphe de g
### BEGIN SOLUTION
x= np.linspace(-5,5,100)
plt.plot(x,g(x))
plt.title("Graphe de $g$")
plt.xlabel("$x$x")
plt.show()
### END SOLUTION

### Question 2

Avec une méthode de type Newton-Cotes, on ne peux pas intégrer sur un intervalle non borné. On considère alors que la fonction $g$ décroit assez rapidement vers 0 en $-\infty$ et en $+\infty$ pour pouvoir approcher l'intégrale

$$
    \int_{-\infty}^{+\infty} \cos(x) e^{-x^2}dx.
$$

par l'intégrale

$$
    \int_{-5}^{5} \cos(x) e^{-x^2}dx.
$$

Tracer l'erreur de quadrature obtenue avec la méthode de Simpson composée sur l'intervalle [-5,5], en fonction du nombre $N$ de sous-intervalles. On prendra $N\in\{1,\dots,11\}$

**Remarque :** la valeur exacte de l'intégrale est $\dfrac{\sqrt{\pi}}{~^4\sqrt{e}} \approx 1.38$.

In [ ]:
### BEGIN SOLUTION
N = np.arange(1,100)
Iexacte = np.sqrt(np.pi)/np.power(np.e,1./4)
E = np.zeros(N.size)
for i in range(N.size):
    E[i] = np.abs(simpson(g,-5,5,N[i])-Iexacte)
    
# Graphe
plt.figure(figsize=[10,8])
plt.title("Erreur de quadrature pour l'intégrale considérée")
plt.loglog(N,E,"+-", label="Simpson composée sur $[-5,5]$")
# Décommenter après avoir exécuter la case de code suivante :
# plt.loglog(N,E2*np.ones(N.size),label="Gauss-Hermite 2 simple sur $\mathbb{R}$")
# plt.loglog(N,E3*np.ones(N.size),label="Gauss-Hermite 3 simple sur $\mathbb{R}$")
plt.legend()
plt.xlabel("$N$")
plt.show()
print("Erreur : ",E)
### END SOLUTION

### Question 3 


Déterminer les polynômes unitaires orthogonaux de degrés 0, 1 et 2 pour ce produit scalaire.

### Réponse

=== BEGIN MARK SCHEME ===
\begin{equation*}
    \begin{array}\\
        p_0(x) & = & 1,\\
        p_1(x) & = & x, \\
        p_2(x) & = & x^2 - \dfrac{1}{2},\\
        p_3(x) & = & x^3 - \dfrac{3}{2}x.
    \end{array}
\end{equation*}
=== END MARK SCHEME ===

### Question 4

Déterminer une formule de quadrature de Gauss simple à partir des racines du polynôme de degré 2 obtenu à la question précédente. Il s'agit de la formule de quadrature de Gauss-Hermite à 2 points.

### Réponse
=== BEGIN MARK SCHEME ===

On peut approcher l'intégrale par $\dfrac{\sqrt{\pi}}{2} \left( f\left(\dfrac{-1}{\sqrt{2}}\right) + f\left(\dfrac{1}{\sqrt{2}}\right) \right)$.

On peut approcher l'intégrale par $\dfrac{\sqrt{\pi}}{6} f\left(\dfrac{-\sqrt{3}}{\sqrt{2}}\right) + \dfrac{2\sqrt{\pi}}{3} f\left(0\right) + \dfrac{\sqrt{\pi}}{6} f\left(\dfrac{\sqrt{3}}{\sqrt{2}}\right)$.

=== END MARK SCHEME ===

### Question 5

Implémenter cette méthode de quadrature simple et donner une valeur approchée de

\begin{equation*}
    \int_{-\infty}^{+\infty} \cos(x) e^{-x^2}dx.
\end{equation*}

Comparer avec la méthode de Simpson composée.

In [ ]:
### BEGIN SOLUTION
def gausshermite2(f):
    return (f(-1./np.sqrt(2)) + f(1./np.sqrt(2)))*np.sqrt(np.pi)/2

def gausshermite3(f):
    return np.sqrt(np.pi)/6.*f(-np.sqrt(3)/np.sqrt(2)) + 2*np.sqrt(np.pi)/3.*f(0) + np.sqrt(np.pi)/6.*f(np.sqrt(3)/np.sqrt(2))

def cos(t):
    return np.cos(t)

E2 = np.abs(gausshermite2(cos)-Iexacte)
print("Erreur de quadrature avec la méthode de \nGauss-Hermite à 2 points : ",E2)

E3 = np.abs(gausshermite3(cos)-Iexacte)
print("Gauss-Hermite à 3 points : ",E3)

# Remarque :
# On observe que la méthode de Gauss-Hermite simple à 2 points permet d'obtenir une approximation de l'intégrale 
# qui ne peut être égalée par la méthode de Simpson composée qu'en prenant au moins 8 sous-intervalles
# de discrétisation sur [-5,5].
#
# Si on va plus loin et qu'on implémente la méthode de Gauss-Hermite simple à 3 points, on voit qu'il faut
# cette fois 10 sous-intervalles avec la méthode de Simpson composée pour obtenir une erreur de 
# quadrature inférieure.
### END SOLUTION

<a id=gauss-tchebychev></a>
## Exercice 3 : Intégrale de fonction singulière

Dans cet exercice, on cherche à calculer une valeur approchée de l'intégrale 

$$ \int_{-1}^1 \dfrac{1+\cos(x)^2}{\sqrt{1-x^2}}dx. $$


### Question 1
Implémenter une méthode de quadrature de Gauss simple d'ordre 5 pour approcher cette intégrale.

***Réponse***

=== BEGIN MARK SCHEME ===

On trouve les polynômes unitaires orthogonaux pour le produit scalaire associé au poids considéré :

$$
    p_0(x) = 1, \\
    p_1(x) = x, \\
    p_2(x) = x^2 - \frac{1}{2},\\
    p_3(x) = x^3 - \frac{3}{4}x.
$$

Les points de quadrature à considérer sur $[-1,1]$ sont les racines de $p_3$, c'est-à-dire les points $-\dfrac{\sqrt{3}}{2}$, 0 et $\dfrac{\sqrt{3}}{2}$.

On calcul alors les poids et on trouve qu'ils valent tous $\frac{\pi}{3}$.

=== END MARK SCHEME ===

In [ ]:
def GaussTchebychev3(f,a,b):
    ### BEGIN SOLUTION
    return np.pi*(f(-np.sqrt(3)/2) + f(0) + f(np.sqrt(3)/2))/3
    ### END SOLUTION

### TEST
### BEGIN SOLUTION

# Pour utiliser la méthode de Gauss-Tchebychev, on définit cette fonction à intégrer
def f3(x):
    return 1

I1 = GaussTchebychev3(f3,-1,1)
print("I1 : solution approchée = ", I1, ", solution exacte = ", 3*np.pi/4.)

### END SOLUTION

### Question 2

Calculer l'erreur de quadrature de cette méthode, pour le calcul de l'intégrale 

$$ \int_{-1}^1 \dfrac{1}{\sqrt{1-x^2}}dx, $$

dont on connaît une valeur exacte et comparer avec la méthode de Gauss-Legendre simple à 2 points.

In [ ]:
### BEGIN SOLUTION

# Pour utiliser la méthode de Gauss-Legendre on définit cette fonction à intégrer
def f4(x):
    return 1./np.sqrt(1-x**2)

N = np.arange(10,100,1)
E1 = np.abs(np.pi-GaussTchebychev3(f3,-1,1))
print("Erreur de quadrature avec GaussTchebychev à 3 points = ",E1)
E2 = np.abs(np.pi - GaussLegendre2(f4,-1,1,1))
print("Erreur de quadrature avec GaussLegendre à 2 points = ",E2)
E3 = np.abs(np.pi - GaussLegendre3(f4,-1,1,1))
print("Erreur de quadrature avec GaussLegendre à 3 points = ",E3)

# Remarque :
# On observe que l'erreur de quadrature avec le méthode de Gauss-Tchebychev est nulle.
# La méthode de quadrature semble exacte pour cette fonction.
# En fait, c'est normal, car le méthode de Gauss-Tchebychev à 3 point est exacte pour des polynôme d'ordre 2.
# Contrairement à une méthode de Newton-Cotes ou de Gauss-Legendre, cette méthode de Gauss-Tchebychev est
# donc exacte pour toute fonction de la forme p(x)/sqrt(1-x^2) avec p un polynome de degré inférieur ou 
# égale à 2.
### END SOLUTION

### Question 3

Déterminer une valeur approchée pour l'intégrale de l'énoncé.

In [ ]:
### BEGIN SOLUTION
# Estimation de l'intégrale avec Gauss-Tchebychev à 3 points
def f5(x):
    return np.cos(x**2) + 1

I5 = GaussTchebychev3(f5,-1,1)
print("Gauss-Tchebychev-3",I5)

# Estimation de l'intégrale avec Gauss-Legendre composée à 3 points et N sous-intervalles
def f6(x):
    return (np.cos(x**2) + 1)/np.sqrt(1-x**2)

N = np.arange(10,10000,10)
I6 = np.zeros(N.size)
for i in range(N.size):
    I6[i]=GaussLegendre3(f6,-1,1,N[i])
    
plt.plot(N,I6,label="Gauss-Legendre-3 (composée)")
plt.plot(N,I5*np.ones(N.size),label="Gauss-Tchebychev-3 (simple)")
plt.legend()
plt.title("Comparaison entre Gauss-Tchebychev à 3 points (simple) et Gauss-Legendre à 3 points (composé) en fonction de N")
plt.show()

# Remarque
# On observe que la méthode de Gauss-Legendre composée à 3 points semble tendre vers
# la valeur donnée par le méthode de Gauss-Tchebychev simple à 3 points.
# Cette méthode de Gauss-Tchebychev simple à 3 points nous donne donc une très bonne
# approximation de l'intégrale (valeur exacte ?)
### END SOLUTION

<a id=EDO></a>
## Exercice 4 : Résolution d'EDO

Dans cet exercice, on s'intéresse à la résolution d'une équation différentielle ordinaire. En particulier, on cherche une fonction $u : [a,b]\subset\mathbb{R} \mapsto \mathbb{R}$, solution de

$$
    u^\prime(t) = \gamma(t)u(t),\\
    u(a) = u_0,
$$

où $\gamma : [a,b] \times \mapsto \mathbb{R}$ est continue sur $[a,b]$ et $u_0 \in \mathbb{R}$ est la condition initiale.

### Question 1

Soit $x\in[a,b]$. Intégrer l'EDO entre $a$ et $x$ et en déduire une équation (intégrale) vérifiée par $u(x)$.

### Réponse

=== BEGIN MARK SCHEME ===
$$
    u(x) = u(a) + \int_a^x \gamma(t)u(t)dt.
$$
=== END MARK SCHEME ===



### Question 2

On considère une subdivision régulière $([x_i-1,x_{i}])_{1\leq i \leq n}$ de $[a,b]$ en $n$ sous-intervalles tels que $x_0=a < x_1 < \dots < x_{n}=b$ et de pas $h$.On cherche alors une approximation de la solution de l'EDO aux points $x_i$, i.e. une approximation de $u(x_i)$.

Pour $i\in\{0,\dots,n\}$, on note $$u_i = u(x_i).$$

À partir de la question précédente et en utilisant la formule de quadrature des rectangles à gauche, déterminer, pour tout $i\geq$, l'expression de $u_i$ en fonction de $u_{i-1}$.

***Remarque***

Cette relation entre $u_i$ et $u_{i-1}$ est ce qu'on appelle un *schéma numérique* pour les EDO. ce schéma en particulier est appellé *schéma d'Euler explicite*. En choisissant une autre formule de quadrature, on obtient un autre schéma numérique.

### Réponse

=== BEGIN MARK SCHEME ===

En appliquant le résultat de la question 1 avec $x=x_i$, on obtient l'équation intégrale

$$
    u(x_i) = u(a) + \int_a^{x_i} \gamma(t)u(t)dt,
$$

c'est-à-dire

$$
    u_i = u_0 + \int_a^{x_i} \gamma(t)u(t)dt.
$$

Sur chaque sous-intervalles $[x_{i-1},x_i]$, on utilise alors la formule des rectangles à gauche pour l'intégrale : 

$$
    \int_a^{x_i} \gamma(t)u(t)dt \approx h \sum_{k=0}^{i-1} \gamma(x_{k})u_{k}.
$$

On obtient alors

$$
    u_i = u_0 + h\sum_{k=0}^{i-1} \gamma(x_{k})u_{k} = u_{i-1} + h\gamma(x_{i-1})u_{i-1} = (1+h\gamma(x_{i-1})) u_{i-1}.
$$

Le schéma d'Euler explicite obtenu est alors le suivant 

$$
    u_0 \text{ est connu},\\
    u_i = (1+h\gamma(x_{i-1})) u_{i-1} \quad \forall i \geq 0.
$$

=== END MARK SCHEME ===

### Question 3

Implémenter le schéma numérique obtenu dans la fonction `schemaEDO1` ci-dessous et résoudre l'équation sur $[0,1]$, en prenant $\gamma(t) = 5$ et $u_0 = 3$

**Remarque**
La fonction devra retourner un tableau numpy $x$ contenant les points de discrétisation de l'intervalle $[a,b]$ et un tableau numpy $u$ contenant les approximation $(u_i)$.

In [ ]:
def schemaEDO(gamma,a,b,N,u0):
    ### BEGIN SOLUTION
    x = np.linspace(a,b,N+1)
    h = x[1]-x[0]
    u = u0*np.ones(x.size)
    for i in range(1,x.size):
        u[i] = u[i-1] + h*gamma(x[i-1])*u[i-1]
    ### END SOLUTION
    return x,u
    

# TEST
### BEGIN SOLUTION
def gamma(x):
    return 5
x,u = schemaEDO(gamma,0,1,100,3)
plt.plot(x,u,"+")
### END SOLUTION

### Question 4

Déterminer la solution exacte de cette EDO et calculer l'erreur de la solution approchée en norme infinie sur l'intervalle $[0,1]$ en fonction du nombre $n$ de sous-intervalles considérés. On tracera ce graphique en échelle logarithmique.

Avez-vous une idée de l'ordre de convergence de cette méthode, i.e. du comportement de la courbe de l'erreur en fonction du pas de dicrétisation ?

In [ ]:
### BEGIN SOLUTION
def solexacte(x):
    return 3*np.exp(5*x)

N = np.arange(10,1000)
E = np.zeros(N.size)
for i in range(N.size):
    x,u = schemaEDO(gamma,0,1,N[i],3)
    ue = solexacte(x)
    E[i] = np.max(np.abs(u-ue))
    
plt.title("Graphique de l'erreur en fonction du nombre de subdivisions")
plt.loglog(N,E,label="Erreur")
plt.loglog(N,1./N,label="Ordre 1")
plt.legend()
plt.xlabel("$N$")
plt.show()
### END SOLUTION

### Question 5

Déterminer et implémenter des schémas numériques en utilisant la formule de quadrature des rectangles à droite et la formule des points milieux.

<a id=2d></a>
## Exercice 5 : Formules de quadrature en 2D

### Question 1

Déterminer une formule de quadrature pour une fonction en deux dimensions $f(x,y)$, qui utilise de l'interpolation polynomiale de degré 0, puis de de degré 1.

Réponse : à vous de bosser !

### Question 2

Définir une méthode de Gauss en deux dimensions.